# EE315 Design Project

Create a Bingo card!

The below method generates an array of random numbers and sorts them into a bingo card format.

Importing the overlay class.

In [1]:
from pynq import Overlay

Program the Overlay onto the PYNQ-Z2, and parse the Hwh file

In [2]:
ol = Overlay("design_1_wrapper.bit")

Return a file that reports the results of the Hwh parsing to the designer.

In [3]:
ol?

Importing the required libraries.

In [4]:
import random
import ipywidgets as widgets
from IPython.display import display
from IPython.display import Audio
from time import sleep
import threading
#from IPython.display import clear_output

In [5]:
rng = ol.rng_test01_0

In [6]:
rng.write(0x00, 0)
rng.write(0x04, 1)
rng.write(0x08,3)
out_address = 0x0C

In [7]:
my_list=[]
for i in range (1,91):
    my_list.append(i)

The call_number_func() ensures that the number generated cannot be greater than 90. If it is then it regenerates it and appends it to a list of random numbers. 

In [8]:
def call_number_func():

    RNG_number = rng.read(out_address)
    while RNG_number>len(my_list):
        RNG_number = rng.read(out_address)
        if RNG_number> len(my_list):
            RNG_number = 90 - len(my_list)
    
    TestNumber=22
    ##filename="./Sounds/"+str(TestNumber)+".mp3" #TestNumber should be RNG_number
    ##display(Audio(filename, autoplay =True))
    
    call_number = my_list[RNG_number]
    my_list.remove(call_number)

    call_list.append(call_number)

In [9]:
call_list=[]

In [38]:
call_number_func()

In [187]:
list(map(int, call_list))

TypeError: 'list' object is not callable

The function implements the ability for the button to change colour. This will allow the user to interact and score off their numbers which have been called. 

In [10]:
button_list=[]
numPress=[]
wrongNumberList=[]

In [11]:
def button_on_click(myButton):
    value=int(myButton.description)

    #//print(num)
    if myButton.style.button_color =='green':
        myButton.style.button_color = 'orange'
        #numPress.remove(myButton.description)
        if not value in call_list:
            delValueFromLists(value)#, numPressLst)            
    else:
        myButton.style.button_color = 'green'
        addValueToLists(value)
        #print(numPressLst)
       # print(myButton.description)
        #print(type(myButton.description))
        #numPress.append(myButton.description)

In [12]:
#def bingo(validation):
#    if(validation):
#        print("Congratulations, you have won!")
#    else:
#        print("Unfortunately, your card is incorrect")     

In [13]:
#numMarked = []
#def numberCalledList(numPress):
    #for noCards in myCards:
        #n = 1
        #numMarked.append(numPress)
        #n = n + 1

In [21]:
def compareValues(numPress, call_list, bingoButton):
    wrongNumberList=[]
    list1=list(map(int, numPress)) #This changes list from strings to ints
    list2=list(map(int, call_list))
    list1 = list(dict.fromkeys(list1)) #converts to dict then back to list to remove duplicates
    check = all(item in list2 for item in list1)
    numReq = 2 #number of numbers required for bingo, 
    
    for element in list1:
        if element not in list2:
            wrongNumberList.append(element)

    if len(list1)==numReq:
        if check is True: 
            print("Congratulations, it's Bingo!")
            display(Audio("./Sounds/ThatsABingo.wav", autoplay =True))
            event.set()
            bingoButton.style.button_color = 'green'
        else:
            print("Unfortunately, these numbers do not match. These numbers are incorrect " + str(wrongNumberList))
            bingoButton.style.button_color = 'red'
            sleep(1)
            bingoButton.style.button_color = "orange"
    else:
        print("Unfortunately, there are not the right amount of numbers for Bingo")
        bingoButton.style.button_color="red"
        sleep(1)
        bingoButton.style.button_color = "orange"

In [44]:
numPress = [1,41]
call_list=[1,41]

In [45]:
compareValues(numPress, call_list)

Congratulations, it's Bingo!


NameError: name 'event' is not defined

In [15]:
def bingoPressed(bingoButton):
    bingoButton
    ind = int(bingoButton.description[-1])-1
    bingoButton.style.button_color = 'blue'
    bingoButton = compareValues(numPressLst[ind], call_list, bingoButton)
   # sleep(1)
   # bingoButton.style.button_color='blue'#

Implementing the bingo card based upon the number of players and size of the card required. 

Through the use of a for loop, the numbers within the card can be generated and placed in a ipywidget layout. This layout creates a grid which is sized using the cardSize * cardSize. 

For the bingo game to be interactive, the need to implement a form of user interaction, such as scoring off the number called, was required. This is achieved by creating a for loop which has a callback element and calls the function above, button_on_click().

In [22]:
cardSize = 4
minNum = 1
maxNum = 90
noCards = 4
myCards = []
bingos = []
cardNumbersList=[]
#numPressLst = [[] for _ in range(noCards)]

for i in range(noCards):
    card = []
    randRange = range(minNum, maxNum)
    card = random.sample(randRange, cardSize * cardSize)
    cardNumbersList.append(card)
    buttons = []
    
    myButton = widgets.GridBox(children=[widgets.Button(description=str(num), layout=widgets.Layout(width='auto', height='auto'),
                 button_style='warning') for num in card],

                layout=widgets.Layout(
                                    width='80%',
                                    grid_template_columns='20%'*cardSize,
                                    grid_template_rows='40px'*cardSize,
                                    grid_gap='1px 2px')
                           )
    
    for button in myButton.children:
        button.on_click(button_on_click)
            
    myCards.append(myButton)
    
  
    
    bingoButton = widgets.GridBox(children=[widgets.Button(description='Bingo - Player'+str(i+1), layout=widgets.Layout(width='auto', height='auto'),
                 button_style='warning')],

                layout=widgets.Layout(
                                    width='60%',
                                    grid_template_columns='20%',
                                    grid_template_rows='40px',
                                    grid_gap='1px 2px')
                            
                                 )
  #  bingoButton = widgets.Button(description='Bingo!', button_style='warning')
    
    for bingo in bingoButton.children:
        bingo.on_click(bingoPressed)

    bingos.append(bingoButton)
    

The bingo card can then be displayed through calling myButton.

In [65]:
for noCards in myCards:
    numPress = []
    

In [66]:
bingo_buttons = []

In [67]:
print(cardNumbersList)


[[26, 48, 69, 1, 35, 29, 61, 54, 80, 89, 20, 62, 51, 22, 76, 7], [26, 60, 88, 71, 14, 66, 5, 62, 87, 28, 56, 84, 13, 18, 36, 33], [16, 11, 4, 83, 45, 82, 44, 62, 42, 14, 20, 74, 56, 50, 31, 88], [70, 47, 45, 25, 85, 11, 73, 15, 20, 32, 5, 77, 19, 81, 62, 6]]


In [18]:

numPressLst = [[] for _ in range(noCards)] #want to have noCards rather than variable but throws error: 'Gridbox object not an integer'

def addValueToLists(value):
    #store = []
    for list in cardNumbersList:
        if value in list:
            print(cardNumbersList.index(list))
            numPressLst[cardNumbersList.index(list)].append(value)
            #store.append(cardNumbersList.index(list))
    #for i in range(0,len(store)):
       # numPressLst[store[i]].append(value)
    print(numPressLst)

#addValueToLists(cardNumbersList,30, numPressLst)
#addValueToLists(30)

In [19]:
def delValueFromLists(value):#, numPressLst):
    for list in numPressLst:
        if value in list:
            list.remove(value)
    print(numPressLst)
#delValueFromLists(71, numPressLst)
print(numPressLst)

[[], [], [], []]


In [27]:
print(call_list)
if not 58 in call_list:
    print("True")

[85, 12, 52, 88, 84, 77, 72]
True


In [199]:
event = threading.Event()


In [203]:
event.set()

In [200]:
def thread_function():
    while(True):
        call_number_func()
        print(call_list[-1]) #-1 just indexes the last element
        sleep(5)
        if len(call_list)==90:
            event.set()
        #clear_output(wait=False)
        if event.is_set():
            break

In [201]:
x = threading.Thread(target=thread_function, args=())
event.clear()
x.start()

27


In [39]:
print(call_list)

[45, 71, 39, 53, 54, 2, 8, 89, 77, 42, 43, 65]


In [24]:
call_list=[32,78]
#numPress =[]

In [23]:
#numPress = []
for idx, card in enumerate(myCards):
    #numPress = myCards[idx]
    display(card)
    display(bingos[idx])
#print(numPress)    
#for idx, card in enumerate(myCards):\n",
        #numPressed = myCards[idx]\n",
        #display(card)
        #for i in range(rows):
            #cols = []
            #for j in cols:
                #cols.append(myButton.description)

GridBox(children=(Button(button_style='warning', description='48', layout=Layout(height='auto', width='auto'),…

GridBox(children=(Button(button_style='warning', description='Bingo - Player1', layout=Layout(height='auto', w…

GridBox(children=(Button(button_style='warning', description='80', layout=Layout(height='auto', width='auto'),…

GridBox(children=(Button(button_style='warning', description='Bingo - Player2', layout=Layout(height='auto', w…

GridBox(children=(Button(button_style='warning', description='6', layout=Layout(height='auto', width='auto'), …

GridBox(children=(Button(button_style='warning', description='Bingo - Player3', layout=Layout(height='auto', w…

GridBox(children=(Button(button_style='warning', description='4', layout=Layout(height='auto', width='auto'), …

GridBox(children=(Button(button_style='warning', description='Bingo - Player4', layout=Layout(height='auto', w…

1
3
[[], [12], [], [12]]
Unfortunately, there are not the right amount of numbers for Bingo
1
3
[[], [12, 38], [], [12, 38]]
Unfortunately, these numbers do not match. These numbers are incorrect [12, 38]
[[], [12], [], [12]]
[[], [], [], []]
Unfortunately, there are not the right amount of numbers for Bingo
2
[[], [], [45], []]
2
[[], [], [45, 70], []]
Unfortunately, these numbers do not match. These numbers are incorrect [45, 70]
[[], [], [45], []]
Unfortunately, there are not the right amount of numbers for Bingo
Unfortunately, there are not the right amount of numbers for Bingo
[[], [], [], []]
2
[[], [], [29], []]
1
2
[[], [51], [29, 51], []]
Unfortunately, these numbers do not match. These numbers are incorrect [29, 51]
[[], [], [29], []]
[[], [], [], []]
3
[[], [], [], [63]]
Unfortunately, there are not the right amount of numbers for Bingo
[[], [], [], []]
0
[[32], [], [], []]
0
[[32, 78], [], [], []]
Congratulations, it's Bingo!


NameError: name 'event' is not defined

In [39]:
bingos

[Button(button_style='warning', description='Bingo!', style=ButtonStyle()),
 Button(button_style='warning', description='Bingo!', style=ButtonStyle()),
 Button(button_style='warning', description='Bingo!', style=ButtonStyle())]

Prints a list of numbers - keep for now just incase. 

buttons = []
#for num in card:
    #print(num)
for num in card:
    print(num)
    myButton = widgets.Button(description=str(num), layout=widgets.Layout(width='100px', height='100px', columns='20%'*cardSize, rows='40px'*cardSize),
                         button_style='danger')

    buttons.append(myButton)
    myButton.on_click(button_on_click)

    
    

for button in buttons:
    display(button)

In [88]:
list(map(int, numPress))

[]

In [89]:
#CheckList=compare_lists(numPress,call_list)

Not enough numbers for Bingo


In [90]:
list(map(int, wrongNumberList))

[]